## CS 132 Homework 5 A 

### Due Thursday August 12th at Midnight (1 minute after 11:59pm) in Gradescope (with grace period of 6 hours)
### Homeworks may be submitted up to 24 hours late with a 10% penalty (same grace period)


Please read through the entire notebook, reading the expository material and then do the problems, following the instuctions to try various features; among the exposition of various features of Python there
are three problems which will be graded. All problems are worth 10 points. 

You will need to complete this notebook and then convert to a PDF file in order to submit to Gradescope. Instructions are given here:

https://www.cs.bu.edu/fac/snyder/cs132/HWSubmissionInstructions.html



In [3]:
# Here are some imports which will be used in the code in the rest of the lab  

# Imports used for the code in CS 237

import numpy as np                # arrays and functions which operate on arrays

import matplotlib.pyplot as plt   # normal plotting


# NOTE: You may not use any other libraries than those listed here without explicit permission.

In [4]:
# Gaussian Elimination

# number of digits of precision to print out

prec = 4

########################################################################################################

# Returns the Row Echelon (upper triangular) form

def forwardElimination(A,traceLevel=0):
    
    A = (np.copy(A)).astype(float)
    
    if (traceLevel > 0):
        print("Running Forward Elimination on:\n")
        print(np.round(A, decimals=4),"\n")
        print()
    
    (numRows,numCols) = A.shape
    
    # r = row we are currently working on         pivot value is A[r][c]
    r = 0            
    for c in range(numCols):     # solve for variable in column c 
        # find row in column c with first non-zero element, and exchange with row r                  
        r1 = r
        while(r1 < numRows):
            if (not np.isclose(A[r1][c],0.0)):   # A[r1][c] is first non-zero element at or below r in column c
                break
            r1 += 1
        
        if(r1 == numRows):    # all zeros below r in this column
            continue          # go on to the next column, but still working on same row   
         
        if(r1 != r): 
            # exchange rows r1 and r
            A[[r1,r],:] = A[[r,r1],:] 
            if (traceLevel == 2): 
                print("Exchange R" + str(r1+1) + " and R" + str(r+1) + "\n") 
                print(np.round(A, decimals=4))                
                print() 

        # now use pivot A[r][c] to eliminate all vars in this column below row r
        for r2 in range(r+1,numRows):
            rowReduce(A,r,c,r2,traceLevel)
            
        r += 1  
        if (r >= numRows):
            break
            
    return A

# for pivot A[r][c], eliminate variable in location A[r2][c] in row r2 using row operations

def rowReduce(A,r,c,r2,traceLevel=0):

    if(not np.isclose(A[r2][c],0.0)):

        factor = -A[r2][c]/A[r][c] 
        A[r2] += factor * A[r]
            
        if(traceLevel == 2):
            print("R" + str(r2+1) + " += " + str(np.around(factor,prec)) + "*R" + str(r+1) + "\n")  
            print(np.round(A, decimals=4))
            print()

# Take a Row Echelon Form and return a Reduced Row Echelon Form

def backwardSubstitute(A,augmented=True,traceLevel=0): 
    
    numRows,numCols = A.shape
    
    if (A.dtype != 'float64'):
        A = A.astype(float)

    # now back-substitute the variables from bottom row to top
    if (traceLevel > 0):
        print("Creating Reduced Row Echelon Form...\n") 

    for r in range(numRows):

        # find variable in this row
        for c in range(numCols):
            if(not np.isclose(A[r][c],0.0)):
                break 
       
        if ((augmented and c >= numCols-1) or (c >= numCols)):        # inconsistent or redundant row
                continue 
                        
        # A[r][c] is variable to eliminate
        
        factor = A[r][c]
        
        if (np.isclose(factor,0.0)):   # already eliminated
            continue
        
        if(not np.isclose(factor,1.0)):  
            A[r] *= 1/factor
            if (traceLevel == 2):
                print("R" + str(r+1) + " = R" + str(r+1) + "/" + str(np.around(factor,prec)) + "\n")  
                print(np.round(A, decimals=4))
                print()

        for r2 in range(r): 
            rowReduce(A,r,c,r2,traceLevel)
            
    return A 

    
# try to find row of all zeros except for last column, in augmented matrix. 

def noSolution(A):
    numRows,numCols = A.shape
    for r in range(numRows-1,-1,-1):         # start from bottom, since inconsistent rows end up there
        for c in range(numCols):
            if(not np.isclose(A[r][c],0.0)):  # found first non-0 in this row
                if(c == numCols-1):
                    return True
                else:
                    break
    return False

########################################################################################################

# Runs GE and returns a reduced row echelon form

# If b == None assumes that A is NOT an augmented matrix, and runs GE and returns Reduced Row Echelon Form

# If b is a column matrix then adjoins it to A and runs GE;
#       Always returns the Reduced Row Echelon Form
#       If inconsistent then also prints out "Inconsistent!"

# If b is a length n array instead of a 1 x n array (column vector)
# b will be converted to a column vector, for convenience. 

# traceLevel 0 will not print anything out during the run
# traceLevel 1 will print out various stages of the process and the intermediate matrices
# traceLevel 2 will also print out the row operations used at each step. 

# If you want to produce an Echelon Form (NOT reduced), then use forwardElimination instead. 

# See examples for more explanation of how to use this

def GaussianElimination(A,b=None, traceLevel = 0):
    if( type(b) != type(None)):
        if( (A.shape)[0] == 1 ):
            b = np.array([b]).T
        Ab = (np.hstack((A.copy(),b))).astype(float)
    else:
        Ab = A.copy().astype(float)
        
    if( traceLevel > 0 and type(b) == type(None)):
        print("Creating Reduced Row Echelon Form:\n")
        print(np.round(Ab, decimals=4))
        print()
    elif( traceLevel > 0 ):
        print("Running Gaussian Elimination on augmented matrix:\n")
        print(np.round(Ab, decimals=4))
        print()
        
    B = forwardElimination(Ab,traceLevel)
    
    if( traceLevel > 0 ):
        print("Echelon Form:\n")
        print( np.round(B, decimals=4) + np.zeros(B.shape),"\n")       # adding -0.0 + 0 gives 0.0
        print()
        
    if ( type(b) != type(None) and noSolution(B) ):
        print("No solution!")

    C = backwardSubstitute(B,type(b)!=type(None),traceLevel)
        
    if( traceLevel > 0 ):
        print("Reduced Row Echelon Form:\n")
        print( np.round(C, decimals=4) + np.zeros(C.shape),"\n")   # adding -0.0 + 0 gives 0.0
        print()
            
    return C

########################################################################################################
  
def GE(A,b=None, traceLevel = 0):
    return GaussianElimination(A,b,traceLevel)

### Problem One



A kindergartner is going through that phase when she only eats certain
foods.   For breakfast she only eats Lucky Charms, Cap'n Crunch, or
Froot Loops.  Her parent notices that if she eats one cereal on a given
day, on the next day she will eat the same cereal with probability of
50\%, and she will choose one of the other cereals with probability of
25\%.

(A) What is the stochastic matrix for this situation? 

(B)  If she chooses Cap'n Crunch on Monday, what is the
  probability she will choose Froot Loops on Wednesday?
  
(C) Consider this question: "If she chooses Lucky Charms on Sunday and Cap'n Crunch on Monday, what is the
  probability she will choose Froot Loops on Wednesday?" The answer to this question is the same as the answer to (B).  Explain carefully why this is the case. 

(D) If the parent would like to predict what cereal the child will eat on some day in the
very distant future, what are the probabilities for each cereal?

For (D), you must run the experiment until it reaches the steady-state vector. Show a trace of the experiment (do not run the experiment much past the steady-state solution, to save space. 


**Solution:**
 

### Problem Two

The weather in Boston is either good, indifferent, or
  bad on any given day.  If the weather is good today, there is a 60\%
  chance the weather will be good tomorrow, a 30\% chance the weather
  will be indifferent, and a 10\% chance the weather will be bad.  If
  the weather is indifferent today, it will be good tomorrow with
  probability 0.40 and indifferent with probability 0.30.  Finally, if
  the weather is bad today it will be good tomorrow with probability
  0.40 and indifferent with probability 0.50. 
  
(A) Give the stochastic matrix for this problem. Order the
    weather types as: (good, indifferent, bad).
  
(B) Suppose there is a 50\% chance of good weather today and a 50\%
    chance of indifferent weather.  What are the chances of bad weather
    tomorrow?
    
(C)  What is the long-term forecast for weather in Boston?  Solve this by using
the algebraic technique shown in lecture for calculating the steady-state
vector directly from the stochastic matrix. 
  
(D) Run an experiment in Python to determined the steady-state vector; it should, of course, be very
close to the result found in (C). Show the trace of the experiment. 

**Solution:**

